## DATA PREPROCESSING

In [2]:
import pandas as pd
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report,confusion_matrix

In [17]:
df = pd.read_excel("category.xlsx",sheet_name= [1,4])
loc_to_cat = df[1]
loc_to_cat['category1'] = loc_to_cat['category1'].str.lower()
allUserData = df[4]
#userData = [df[3], df[4], df[5], df[6], df[7]]

#for i in userData[1:]:
#    allUserData = allUserData.append(i)
allUserData.head()

user_id  weekday       date start_time   end_date  end_time  duration  \
0        2        2 2020-06-29   16:00:00 2020-06-29  19:00:00  03:00:00   
1        2        2 2020-06-29   19:00:00 2020-06-29  20:00:00  01:00:00   
2        2        2 2020-06-29   20:00:00 2020-06-29  20:30:00  00:30:00   
3        2        2 2020-06-29   20:30:00 2020-06-29  21:30:00  01:00:00   
4        2        2 2020-06-29   21:30:00 2020-06-29  23:30:00  02:00:00   

   category  category_id location_name location_category my_place  \
0   meeting           13           路易莎              cafe      NaN   
1      food            1        全哥鵝肉小炒        restaurant      NaN   
2   leisure           10           NaN               NaN     home   
3  shopping           12       Miramar     Shopping mall      NaN   
4     study            5           NaN               NaN     home   

   location_id  place_id  
0          4.0       NaN  
1          5.0       NaN  
2          NaN       1.0  
3          6.0       NaN  
4          NaN       1.0

In [18]:
allUserData['location']= allUserData['location_id'].combine_first(allUserData['place_id'])
#drop commute
indexNames = allUserData[(allUserData['category_id'] == 17) ].index
allUserData.drop(indexNames,inplace=True)

allUserData['location'].fillna("99", inplace = True)
allUserData = allUserData.drop(['date','end_date','end_time','location_name','location_category','my_place','location_id','place_id'], 1)
allUserData = allUserData.reset_index(drop = True)

In [19]:
def get_hours(ts):
    a = ts.hour
    return a

def get_mins(ts):
    a = ts.minute
    return a

def get_duration(ts):
    a = ts.hour*60 + ts.minute
    return a 

#allUserData['start_mins'] = allUserData['start_time'].apply(get_mins)
allUserData['start_time'] = allUserData['start_time'].apply(get_duration)
allUserData['duration'] = allUserData['duration'].apply(get_duration)
allUserData = allUserData[['user_id','weekday','start_time','duration','location','category','category_id']]
allUserData.tail()

user_id  weekday  start_time  duration location category  category_id
444        2        5          50       495        1    sleep            3
445        2        5         545        15        1  leisure           10
446        2        5         570       150        2     work            6
447        2        5         780       360        3  meeting           13
448        2        5        1200       240        1  leisure           10

## Random Forest Model

In [28]:
train_df = allUserData.loc[0:299]
test_df = allUserData.loc[300:]
print("Number of traing data is :",len(train_df))
print("Number of testing data is :",len(test_df))

Number of traing data is : 300
Number of testing data is : 149


In [29]:
# without diff
X_train = train_df.iloc[:, np.r_[0:4]].values
y_train = train_df.iloc[:, 6].values

X_test = test_df.iloc[:, np.r_[0:4]].values
y_test = test_df.iloc[:, 6].values

In [30]:
clf = RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=2, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
            oob_score=False, random_state=50, verbose=0,
            warm_start=False)
clf.fit(X_train, y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=2, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
            oob_score=False, random_state=50, verbose=0, warm_start=False)

In [31]:
clf.score(X_test, y_test)

0.6308724832214765

In [32]:
imp = clf.feature_importances_
imp

array([0.        , 0.11707604, 0.48461265, 0.3983113 ])

In [26]:
predictions = clf.predict(X_test)
print(classification_report(y_test,predictions))

              precision    recall  f1-score   support

           1       0.36      0.71      0.48        21
           3       1.00      0.95      0.97        19
           4       0.00      0.00      0.00         0
           6       0.50      0.82      0.62        11
           9       0.80      0.80      0.80         5
          10       0.80      0.71      0.75        58
          11       0.50      0.12      0.20         8
          12       0.44      0.25      0.32        16
          13       1.00      0.33      0.50         6
          16       0.00      0.00      0.00         2
          18       0.00      0.00      0.00         3

   micro avg       0.63      0.63      0.63       149
   macro avg       0.49      0.43      0.42       149
weighted avg       0.67      0.63      0.62       149



/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/sklearn/metrics/classification.py:1145: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)


In [27]:
print(confusion_matrix(y_test,predictions))

[[15  0  0  0  0  4  1  1  0  0  0]
 [ 0 18  0  0  0  1  0  0  0  0  0]
 [ 0  0  0  0  0  0  0  0  0  0  0]
 [ 0  0  0  9  0  1  0  0  0  1  0]
 [ 0  0  0  0  4  1  0  0  0  0  0]
 [ 8  0  1  5  0 41  0  3  0  0  0]
 [ 5  0  0  0  0  2  1  0  0  0  0]
 [10  0  0  0  1  1  0  4  0  0  0]
 [ 0  0  0  4  0  0  0  0  2  0  0]
 [ 2  0  0  0  0  0  0  0  0  0  0]
 [ 2  0  0  0  0  0  0  1  0  0  0]]


In [33]:
predictions

array([12,  1,  1, 10, 10, 10,  3, 10, 10,  1, 10, 11,  1,  1,  4, 10,  3,
       10,  6, 10, 10, 10, 10,  1,  6,  1, 12, 10, 10,  3,  6,  6, 10,  9,
       10,  3,  6,  1,  1, 13, 10, 10,  9, 10,  3,  6,  6,  1, 10, 10,  3,
       10,  1,  1, 12,  1,  1, 11,  1, 10,  3, 10,  3, 10, 12, 12,  1,  6,
        1,  1, 12,  1, 10,  3, 10,  6,  1, 10, 12,  9, 10,  3,  6,  6,  1,
       10,  9, 10, 10,  3, 10,  6,  1, 13,  1,  1,  1, 10, 10,  3, 10,  1,
       16,  1, 10,  3, 10,  1,  1, 10,  1,  1,  1, 10,  3, 10,  1, 10, 12,
       10,  3, 10,  6,  1, 12, 10,  3, 10,  1,  6,  1, 10,  3,  6,  6,  1,
        1,  1,  1,  1,  1, 10,  9, 10,  3, 10,  6,  6, 10])

## User Data

In [695]:
location = pd.read_csv("0915.csv")
location.tail()

location_id   longitude   latitude  start_date start_time  weekday  \
3138         3139  121.576946  24.987183  2020-09-15      14:59        3   
3139         3140  121.577937  24.987118  2020-09-15      15:05        3   
3140         3141  121.577796  24.988042  2020-09-15      15:05        3   
3141         3142  121.576811  24.987780  2020-09-15      15:05        3   
3142         3143  121.576522  24.986908  2020-09-15      15:07        3   

      duration     speed                         name1  \
3138       0.0  2.439125      NCCU College of Commerce   
3139       0.0 -1.000000  National Chengchi University   
3140       0.0 -1.000000  National Chengchi University   
3141       0.0  2.078221                      Crêperie   
3142       0.0  2.112187      NCCU College of Commerce   

                             name2                         name3  \
3138  National Chengchi University        NCCU International MBA   
3139                          滇味廚房                   國立政治大學達賢圖書館   
3140                   國立政治大學達賢圖書館                          滇味廚房   
3141                        永康街左撇子              佳佳影印店-論文/打字/紙張專賣   
3142                        Hilife  National Chengchi University   

                                               name4                   name5  \
3138                                          Hilife                     逸仙樓   
3139                                            莊敬三舍                  金鮨日式料理   
3140  National Chengchi University (United Hospital)                7-Eleven   
3141                                          5 Cafe              全家便利商店 政富店   
3142                                   國立政治大學商學院圖書分館  NCCU International MBA   

       category1          category2          category3          category4  \
3138  university         university  point_of_interest  convenience_store   
3139  university         restaurant            library  point_of_interest   
3140  university            library         restaurant    transit_station   
3141  restaurant         restaurant  point_of_interest             bakery   
3142  university  convenience_store         university            library   

              category5  
3138             school  
3139         restaurant  
3140  convenience_store  
3141  convenience_store  
3142  point_of_interest

In [706]:
stopLoc = location.drop(['category3','category4','category5'], 1)

# def string_to_mins(ts):
#     a = int(ts.split(':')[0])
#     b = int(ts.split(':')[1])
#     c = a*60 + b
#     return c

#stopLoc['start_time'] = pd.to_datetime(stopLoc['start_time'], format='%H:%M', errors='ignore').apply(string_to_mins)
stopLoc['longitude'] = round(stopLoc['longitude'],3)
stopLoc['latitude'] = round(stopLoc['latitude'],3)
stopLoc = stopLoc.loc[stopLoc['name1'] != 'nccu dorm9']
stopLoc = stopLoc.reset_index(drop = True) 

In [707]:
#刪掉enter跟exit中的資料
enterList = []
dropList = []

for a in range(len(stopLoc)):
    
    #如果這筆是「enter」，記住編號
    if (stopLoc.iloc[a,14] == 'entering myPlace'):
        enterList.append(a)
                
    #如果這筆是「exit」，清空enterList
    elif (stopLoc.iloc[a,14] == 'exiting myPlace'):
        enterList = []
            
    elif (enterList == []):
        pass
            
    #如果這筆不是進去也不是出來，且有enterList，為要刪除的東西
    elif (enterList != []):
        dropList.append(a) 

stopLoc = stopLoc.drop(dropList)
stopLoc = stopLoc.reset_index(drop = True)  

In [708]:
#刪掉enter跟exit中的資料
enterList = []
dropList = []

for a in range(len(stopLoc)):
    
    #如果這筆是「enter」，記住編號
    if (stopLoc.iloc[a,14] == 'entering commonPlace'):
        enterList.append(a)
                
    #如果這筆是「exit」，清空enterList
    elif (stopLoc.iloc[a,14] == 'exiting commonPlace'):
        enterList = []
            
    elif (enterList == []):
        pass
            
    #如果這筆不是進去也不是出來，且有enterList，為要刪除的東西
    elif (enterList != []):
        dropList.append(a) 

stopLoc = stopLoc.drop(dropList)
stopLoc = stopLoc.reset_index(drop = True)  
stopLoc

location_id  longitude  latitude  start_date start_time  weekday  \
0               1    121.576    24.986  2020/07/22      11:00        4   
1               2    121.443    24.433  2020/07/23      12:00        5   
2               3    121.123    24.765  2020/07/24    13:00\n        6   
3               4    121.563    25.087  2020-09-10      00:25        5   
4               5    121.563    25.087  2020-09-10      00:25        5   
5               6    121.563    25.087  2020-09-10      00:25        5   
6               7    121.563    25.087  2020-09-10      00:25        5   
7               8    121.563    25.087  2020-09-10      10:17        5   
8               9    121.563    25.087  2020-09-10      10:17        5   
9              10    121.563    25.087  2020-09-10      10:17        5   
10             11    121.563    25.087  2020-09-10      10:17        5   
11             12    121.563    25.087  2020-09-10      10:38        5   
12             13    121.563    25.087  2020-09-10      10:38        5   
13             14    121.563    25.087  2020-09-10      10:38        5   
14             15    121.563    25.087  2020-09-10      10:38        5   
15             16    121.563    25.087  2020-09-10      10:38        5   
16             17    121.563    25.086  2020-09-10      11:07        5   
17             18    121.562    25.086  2020-09-10      11:08        5   
18             19    121.561    25.085  2020-09-10      11:09        5   
19             20    121.563    25.087  2020-09-10      11:10        5   
20             21    121.563    25.083  2020-09-10      11:12        5   
21             22    121.563    25.083  2020-09-10      11:12        5   
22             23    121.563    25.083  2020-09-10      11:12        5   
23             24    121.564    25.083  2020-09-10      11:12        5   
24             25    121.564    25.083  2020-09-10      11:12        5   
25             26    121.565    25.082  2020-09-10      11:12        5   
26             27    121.565    25.081  2020-09-10      11:13        5   
27             28    121.565    25.081  2020-09-10      11:13        5   
28             29    121.566    25.080  2020-09-10      11:14        5   
29             30    121.567    25.080  2020-09-10      11:14        5   
30             31    121.568    25.079  2020-09-10      11:15        5   
31             32    121.569    25.079  2020-09-10      11:15        5   
32             33    121.570    25.078  2020-09-10      11:15        5   
33             34    121.571    25.078  2020-09-10      11:16        5   
34             35    121.572    25.078  2020-09-10      11:16        5   
35             36    121.573    25.077  2020-09-10      11:17        5   
36             37    121.573    25.077  2020-09-10      11:17        5   
37             38    121.574    25.077  2020-09-10      11:17        5   
38             39    121.575    25.076  2020-09-10      11:18        5   
39             40    121.576    25.076  2020-09-10      11:18        5   
40             41    121.576    25.075  2020-09-10      11:18        5   
41             42    121.577    25.075  2020-09-10      11:19        5   
42             43    121.578    25.074  2020-09-10      11:20        5   
43             44    121.579    25.074  2020-09-10      11:20        5   
44             45    121.580    25.073  2020-09-10      11:21        5   
45             46    121.580    25.072  2020-09-10      11:21        5   
46             47    121.581    25.072  2020-09-10      11:21        5   
47             48    121.582    25.071  2020-09-10      11:22        5   
48             49    121.582    25.071  2020-09-10      11:22        5   
49             50    121.583    25.070  2020-09-10      11:22        5   
50             51    121.583    25.070  2020-09-10      11:23        5   
51             52    121.584    25.069  2020-09-10      11:23        5   
52             53    121.583    25.069  2020-09-10      11:23        5   
53        

In [709]:
for row in range(0,len(stopLoc)-1): 

    #calculate duration
    if stopLoc.iloc[row+1,3] == stopLoc.iloc[row,3]:
        stopLoc.iloc[row,6] = datetime.strptime(stopLoc.iloc[row+1,4], '%H:%M') - datetime.strptime(stopLoc.iloc[row,4], '%H:%M')       
    else:
        a = dt.datetime(2000,1,2,int(stopLoc.iloc[row+1,4].split(':')[0]),int(stopLoc.iloc[row+1,4].split(':')[1]))
        b = dt.datetime(2000,1,1,int(stopLoc.iloc[row,4].split(':')[0]),int(stopLoc.iloc[row,4].split(':')[1]))
        stopLoc.iloc[row,6] = a - b

#delete trivial data, 重複地點太多刪除
dropList = []
for row in range(1,len(stopLoc)-1): 
    if stopLoc.iloc[row,14] != 'entering myPlace' and stopLoc.iloc[row,14] != 'exiting myPlace':
        
        #same longitude and lantitude
        if stopLoc.iloc[row,1] == stopLoc.iloc[row-1,1] and stopLoc.iloc[row,2] == stopLoc.iloc[row-1,2]:
            dropList.append(row)

        #compared with the last record, over 2 place name duplicated will be deleted
        res = set(stopLoc.iloc[row,8:13]) & set(stopLoc.iloc[row-1,8:13])
        if stopLoc.iloc[row-1,6] < pd.Timedelta('00:10:00'):
            if len(res) > 1: 
                dropList.append(row)

stopLoc = stopLoc.drop(dropList)
stopLoc = stopLoc.reset_index(drop = True)
stopLoc

location_id  longitude  latitude  start_date start_time  weekday  \
0               1    121.576    24.986  2020/07/22      11:00        4   
1               2    121.443    24.433  2020/07/23      12:00        5   
2               3    121.123    24.765  2020/07/24    13:00\n        6   
3               4    121.563    25.087  2020-09-10      00:25        5   
4              17    121.563    25.086  2020-09-10      11:07        5   
5              18    121.562    25.086  2020-09-10      11:08        5   
6              19    121.561    25.085  2020-09-10      11:09        5   
7              20    121.563    25.087  2020-09-10      11:10        5   
8              21    121.563    25.083  2020-09-10      11:12        5   
9              24    121.564    25.083  2020-09-10      11:12        5   
10             26    121.565    25.082  2020-09-10      11:12        5   
11             27    121.565    25.081  2020-09-10      11:13        5   
12             29    121.566    25.080  2020-09-10      11:14        5   
13             30    121.567    25.080  2020-09-10      11:14        5   
14             31    121.568    25.079  2020-09-10      11:15        5   
15             32    121.569    25.079  2020-09-10      11:15        5   
16             33    121.570    25.078  2020-09-10      11:15        5   
17             34    121.571    25.078  2020-09-10      11:16        5   
18             35    121.572    25.078  2020-09-10      11:16        5   
19             39    121.575    25.076  2020-09-10      11:18        5   
20             40    121.576    25.076  2020-09-10      11:18        5   
21             41    121.576    25.075  2020-09-10      11:18        5   
22             42    121.577    25.075  2020-09-10      11:19        5   
23             43    121.578    25.074  2020-09-10      11:20        5   
24             44    121.579    25.074  2020-09-10      11:20        5   
25             46    121.580    25.072  2020-09-10      11:21        5   
26             48    121.582    25.071  2020-09-10      11:22        5   
27             50    121.583    25.070  2020-09-10      11:22        5   
28             52    121.584    25.069  2020-09-10      11:23        5   
29             53    121.583    25.069  2020-09-10      11:23        5   
30             54    121.582    25.068  2020-09-10      11:23        5   
31             57    121.579    25.067  2020-09-10      11:24        5   
32             58    121.578    25.067  2020-09-10      11:24        5   
33             59    121.577    25.066  2020-09-10      11:24        5   
34             64    121.572    25.065  2020-09-10      11:25        5   
35             70    121.566    25.063  2020-09-10      11:26        5   
36             71    121.565    25.063  2020-09-10      11:26        5   
37             72    121.564    25.063  2020-09-10      11:26        5   
38             77    121.560    25.063  2020-09-10      11:28        5   
39             82    121.555    25.062  2020-09-10      11:28        5   
40             88    121.550    25.060  2020-09-10      11:32        5   
41             92    121.549    25.057  2020-09-10      11:33        5   
42             95    121.549    25.054  2020-09-10      11:35        5   
43             96    121.549    25.053  2020-09-10      11:35        5   
44             97    121.549    25.052  2020-09-10      11:35        5   
45            100    121.551    25.052  2020-09-10      11:39        5   
46            101    121.552    25.052  2020-09-10      11:40        5   
47            102    121.553    25.052  2020-09-10      11:43        5   
48            103    121.553    25.053  2020-09-10      11:44        5   
49            104    121.554    25.053  2020-09-10      11:45        5   
50            106    121.555    25.054  2020-09-10      11:46        5   
51            111    121.555    25.053  2020-09-10      11:57        5   
52            112    121.555    25.052  2020-09-10      12:44        5   
53        

In [710]:
pd.set_option('display.max_rows', 5000)

In [711]:
#kill duration < 10 mins, and keep the start of commuting
import datetime as dt
from datetime import datetime

dropList = []
for row in range(0,len(stopLoc)-1): 

    #calculate duration
    if stopLoc.iloc[row+1,3] == stopLoc.iloc[row,3]:
        stopLoc.iloc[row,6] = datetime.strptime(stopLoc.iloc[row+1,4], '%H:%M') - datetime.strptime(stopLoc.iloc[row,4], '%H:%M')       
    else:
        a = dt.datetime(2000,1,2,int(stopLoc.iloc[row+1,4].split(':')[0]),int(stopLoc.iloc[row+1,4].split(':')[1]))
        b = dt.datetime(2000,1,1,int(stopLoc.iloc[row,4].split(':')[0]),int(stopLoc.iloc[row,4].split(':')[1]))
        stopLoc.iloc[row,6] = a - b
            
    #kill duration <10
    if pd.Timedelta(stopLoc.iloc[row,6]) < pd.Timedelta('00:10:00'):
        if stopLoc.iloc[row,14] != 'entering myPlace' and stopLoc.iloc[row,14] != 'exiting myPlace':
            dropList.append(row)    
            
removeList = []
for i in range(1,len(dropList)-1):
    if dropList[i] - dropList[i-1] < 2:
        removeList.append(dropList[i])

stopLoc = stopLoc.drop(removeList)
stopLoc = stopLoc.reset_index(drop = True)
stopLoc

location_id  longitude  latitude  start_date start_time  weekday  \
0              1    121.576    24.986  2020/07/22      11:00        4   
1              2    121.443    24.433  2020/07/23      12:00        5   
2              3    121.123    24.765  2020/07/24    13:00\n        6   
3              4    121.563    25.087  2020-09-10      00:25        5   
4             17    121.563    25.086  2020-09-10      11:07        5   
5             20    121.563    25.087  2020-09-10      11:10        5   
6             21    121.563    25.083  2020-09-10      11:12        5   
7            106    121.555    25.054  2020-09-10      11:46        5   
8            111    121.555    25.053  2020-09-10      11:57        5   
9            112    121.555    25.052  2020-09-10      12:44        5   
10           122    121.554    25.052  2020-09-10      18:21        5   
11           129    121.578    25.051  2020-09-10      18:39        5   
12           132    121.577    25.051  2020-09-10      18:55        5   
13           133    121.576    25.051  2020-09-10      18:58        5   
14           134    121.575    25.050  2020-09-10      19:09        5   
15           135    121.574    25.050  2020-09-10      19:11        5   
16           136    121.575    25.050  2020-09-10      19:21        5   
17           139    121.577    25.051  2020-09-10      19:31        5   
18           140    121.578    25.051  2020-09-10      19:48        5   
19           156    121.577    25.064  2020-09-10      19:57        5   
20           164    121.575    25.063  2020-09-10      21:02        5   
21           200    121.563    25.087  2020-09-10      21:10        5   
22           226    121.563    25.087  2020-09-11      09:15        6   
23           227    121.560    25.085  2020-09-11      09:15        6   
24           305    121.517    25.048  2020-09-11      09:45        6   
25           306    121.516    25.049  2020-09-11      09:59        6   
26           473    120.726    24.508  2020-09-11      11:04        6   
27           476    120.615    24.102  2020-09-11      11:19        6   
28           607    120.286    22.925  2020-09-11      12:11        6   
29           621    120.281    22.927  2020-09-11      12:23        6   
30           895    120.199    22.996  2020-09-11      13:58        6   
31           897    120.199    22.995  2020-09-11      14:20        6   
32          1049    120.202    22.997  2020-09-11      15:06        6   
33          1052    120.204    22.997  2020-09-11      15:28        6   
34          1129    120.172    22.997  2020-09-11      15:54        6   
35          1132    120.171    22.996  2020-09-11      16:35        6   
36          1170    120.200    22.987  2020-09-11      16:49        6   
37          1172    120.198    22.987  2020-09-11      17:20        6   
38          1173    120.199    22.987  2020-09-11      18:19        6   
39          1209    120.194    23.009  2020-09-11      18:43        6   
40          1214    120.192    23.008  2020-09-11      19:07        6   
41          1239    120.192    23.017  2020-09-11      19:21        6   
42          1240    120.193    23.018  2020-09-11      19:38        6   
43          1241    120.193    23.017  2020-09-11      20:31        6   
44          1242    120.194    23.018  2020-09-11      22:14        6   
45          1245    120.192    23.017  2020-09-11      22:41        6   
46          1246    120.193    23.018  2020-09-11      22:41        6   
47          1250    120.193    23.018  2020-09-11      22:57        6   
48          1255    120.193    23.017  2020-09-11      23:03        6   
49          1257    120.193    23.018  2020-09-11      23:44        6   
50          1258    120.192    23.018  2020-09-12      00:04        7   
51          1279    120.195    23.017  2020-09-12      00:39        7   
52          1281    120.193    23.018  2020-09-12      00:59        7   
53          1287    120.193    23.017  2020-09-12      01:02   

In [712]:
#delete duplicate:重複進出同地點, 刪時間短的,重算時間
duplicate = []
for row in range(0,len(stopLoc)-1): 
    
    if (stopLoc.iloc[row,14] == 'exiting myPlace') and (stopLoc.iloc[row+2,14] == 'entering myPlace'):
        if (stopLoc.iloc[row,8] == stopLoc.iloc[row+2,8]):
            duplicate.extend([row,row+1,row+2])
    
    #kill duration <10
    if pd.Timedelta(stopLoc.iloc[row,6]) < pd.Timedelta('00:10:00'):
        if stopLoc.iloc[row,14] != 'entering myPlace' and stopLoc.iloc[row,14] != 'exiting myPlace':
            duplicate.append(row) 

stopLoc = stopLoc.drop(duplicate)
stopLoc = stopLoc.reset_index(drop = True)
            
for row in range(0,len(stopLoc)-1): 
    #calculate duration
    if stopLoc.iloc[row+1,3] == stopLoc.iloc[row,3]:
        stopLoc.iloc[row,6] = datetime.strptime(stopLoc.iloc[row+1,4], '%H:%M') - datetime.strptime(stopLoc.iloc[row,4], '%H:%M')       
    else:
        a = dt.datetime(2000,1,2,int(stopLoc.iloc[row+1,4].split(':')[0]),int(stopLoc.iloc[row+1,4].split(':')[1]))
        b = dt.datetime(2000,1,1,int(stopLoc.iloc[row,4].split(':')[0]),int(stopLoc.iloc[row,4].split(':')[1]))
        stopLoc.iloc[row,6] = a - b

stopLoc

location_id  longitude  latitude  start_date start_time  weekday  \
0             1    121.576    24.986  2020/07/22      11:00        4   
1             2    121.443    24.433  2020/07/23      12:00        5   
2             3    121.123    24.765  2020/07/24    13:00\n        6   
3             4    121.563    25.087  2020-09-10      00:25        5   
4            20    121.563    25.087  2020-09-10      11:10        5   
5           106    121.555    25.054  2020-09-10      11:46        5   
6           111    121.555    25.053  2020-09-10      11:57        5   
7           112    121.555    25.052  2020-09-10      12:44        5   
8           129    121.578    25.051  2020-09-10      18:39        5   
9           133    121.576    25.051  2020-09-10      18:58        5   
10          135    121.574    25.050  2020-09-10      19:11        5   
11          139    121.577    25.051  2020-09-10      19:31        5   
12          156    121.577    25.064  2020-09-10      19:57        5   
13          200    121.563    25.087  2020-09-10      21:10        5   
14          226    121.563    25.087  2020-09-11      09:15        6   
15          305    121.517    25.048  2020-09-11      09:45        6   
16          473    120.726    24.508  2020-09-11      11:04        6   
17          607    120.286    22.925  2020-09-11      12:11        6   
18          895    120.199    22.996  2020-09-11      13:58        6   
19         1049    120.202    22.997  2020-09-11      15:06        6   
20         1129    120.172    22.997  2020-09-11      15:54        6   
21         1170    120.200    22.987  2020-09-11      16:49        6   
22         1172    120.198    22.987  2020-09-11      17:20        6   
23         1209    120.194    23.009  2020-09-11      18:43        6   
24         1239    120.192    23.017  2020-09-11      19:21        6   
25         1240    120.193    23.018  2020-09-11      19:38        6   
26         1241    120.193    23.017  2020-09-11      20:31        6   
27         1242    120.194    23.018  2020-09-11      22:14        6   
28         1246    120.193    23.018  2020-09-11      22:41        6   
29         1255    120.193    23.017  2020-09-11      23:03        6   
30         1257    120.193    23.018  2020-09-11      23:44        6   
31         1258    120.192    23.018  2020-09-12      00:04        7   
32         1279    120.195    23.017  2020-09-12      00:39        7   
33         1287    120.193    23.017  2020-09-12      01:02        7   
34         1291    120.192    23.017  2020-09-12      01:43        7   
35         1292    120.192    23.016  2020-09-12      01:57        7   
36         1303    120.193    23.017  2020-09-12      02:50        7   
37         1310    120.193    23.017  2020-09-12      11:50        7   
38         1348    120.208    22.992  2020-09-12      12:07        7   
39         1422    120.232    22.980  2020-09-12      13:56        7   
40         1484    120.201    22.992  2020-09-12      16:24        7   
41         1491    120.198    22.987  2020-09-12      16:42        7   
42         1497    120.201    22.992  2020-09-12      17:13        7   
43         1531    120.199    22.987  2020-09-12      18:40        7   
44         1533    120.199    22.987  2020-09-12      18:56        7   
45         1536    120.199    22.987  2020-09-12      19:39        7   
46         1538    120.199    22.987  2020-09-12      19:52        7   
47         1584    120.193    23.017  2020-09-12      20:30        7   
48         1595    120.193    23.017  2020-09-13      12:08        1   
49         1605    120.193    23.009  2020-09-13      12:10        1   
50         1626    120.193    22.993  2020-09-13      13:10        1   
51         1709    120.283    22.922  2020-09-13      13:54        1   
52         1726    120.279    23.148  2020-09-13      14:36        1   
53         1847    120.666    24.296  2020-09-13      15:15        1   
54         1998    121.563    25.087  2020-0

In [713]:
#delete trivial data, 重複地點太多刪除

dropList = []
for row in range(1,len(stopLoc)-1): 
    if stopLoc.iloc[row,14] != 'entering myPlace' and stopLoc.iloc[row,14] != 'exiting myPlace':
        
        #same longitude and lantitude
        if stopLoc.iloc[row,1] == stopLoc.iloc[row-1,1] and stopLoc.iloc[row,2] == stopLoc.iloc[row-1,2]:
            dropList.append(row)

        #compared with the last record, over 2 place name duplicated will be deleted
        res = set(stopLoc.iloc[row,8:13]) & set(stopLoc.iloc[row-1,8:13])
        if len(res) > 1: 
            dropList.append(row)

stopLoc = stopLoc.drop(dropList)
stopLoc = stopLoc.drop(['name3','name4','name5'], 1)
stopLoc = stopLoc.reset_index(drop = True)

for row in range(0,len(stopLoc)-1): 
    #calculate duration
    if stopLoc.iloc[row+1,3] == stopLoc.iloc[row,3]:
        stopLoc.iloc[row,6] = datetime.strptime(stopLoc.iloc[row+1,4], '%H:%M') - datetime.strptime(stopLoc.iloc[row,4], '%H:%M')       
    else:
        a = dt.datetime(2000,1,2,int(stopLoc.iloc[row+1,4].split(':')[0]),int(stopLoc.iloc[row+1,4].split(':')[1]))
        b = dt.datetime(2000,1,1,int(stopLoc.iloc[row,4].split(':')[0]),int(stopLoc.iloc[row,4].split(':')[1]))
        stopLoc.iloc[row,6] = a - b

In [714]:
#標commute
twtymin = pd.Timedelta('00:20:00')

for row in range(0,len(stopLoc)-1): 

    if stopLoc.iloc[row,11] != 'entering myPlace':
        #mark as commute if distance bigger than 500 meters. 
        if (abs(stopLoc.iloc[row+1,1] - stopLoc.iloc[row,1]) + abs(stopLoc.iloc[row+1,2] - stopLoc.iloc[row,2])) > 0.04:
            stopLoc.iloc[row,10] = 'commute'
            
#         elif (abs(stopLoc.iloc[row-1,1] - stopLoc.iloc[row,1]) + abs(stopLoc.iloc[row-1,2] - stopLoc.iloc[row,2])) > 0.02:
#             stopLoc.iloc[row,7] = 'commute'
            
        if stopLoc.iloc[row,11] == 'exiting myPlace':
            stopLoc.iloc[row,10] = 'commute' 
            
        if pd.Timedelta(stopLoc.iloc[row-1,7]) > twtymin :
            if abs(stopLoc.iloc[row-1,1] - stopLoc.iloc[row,1]) > 0.02 or abs(stopLoc.iloc[row-1,2] - stopLoc.iloc[row,2]) > 0.02:
                stopLoc.iloc[row,10] = 'commute'        
        
stopLoc

location_id  longitude  latitude  start_date start_time  weekday  \
0             1    121.576    24.986  2020/07/22      11:00        4   
1             2    121.443    24.433  2020/07/23      12:00        5   
2             3    121.123    24.765  2020/07/24    13:00\n        6   
3             4    121.563    25.087  2020-09-10      00:25        5   
4            20    121.563    25.087  2020-09-10      11:10        5   
5           106    121.555    25.054  2020-09-10      11:46        5   
6           111    121.555    25.053  2020-09-10      11:57        5   
7           112    121.555    25.052  2020-09-10      12:44        5   
8           129    121.578    25.051  2020-09-10      18:39        5   
9           133    121.576    25.051  2020-09-10      18:58        5   
10          135    121.574    25.050  2020-09-10      19:11        5   
11          139    121.577    25.051  2020-09-10      19:31        5   
12          156    121.577    25.064  2020-09-10      19:57        5   
13          200    121.563    25.087  2020-09-10      21:10        5   
14          226    121.563    25.087  2020-09-11      09:15        6   
15          305    121.517    25.048  2020-09-11      09:45        6   
16          473    120.726    24.508  2020-09-11      11:04        6   
17          607    120.286    22.925  2020-09-11      12:11        6   
18          895    120.199    22.996  2020-09-11      13:58        6   
19         1049    120.202    22.997  2020-09-11      15:06        6   
20         1129    120.172    22.997  2020-09-11      15:54        6   
21         1170    120.200    22.987  2020-09-11      16:49        6   
22         1172    120.198    22.987  2020-09-11      17:20        6   
23         1209    120.194    23.009  2020-09-11      18:43        6   
24         1239    120.192    23.017  2020-09-11      19:21        6   
25         1240    120.193    23.018  2020-09-11      19:38        6   
26         1241    120.193    23.017  2020-09-11      20:31        6   
27         1246    120.193    23.018  2020-09-11      22:41        6   
28         1279    120.195    23.017  2020-09-12      00:39        7   
29         1303    120.193    23.017  2020-09-12      02:50        7   
30         1310    120.193    23.017  2020-09-12      11:50        7   
31         1348    120.208    22.992  2020-09-12      12:07        7   
32         1422    120.232    22.980  2020-09-12      13:56        7   
33         1484    120.201    22.992  2020-09-12      16:24        7   
34         1491    120.198    22.987  2020-09-12      16:42        7   
35         1497    120.201    22.992  2020-09-12      17:13        7   
36         1531    120.199    22.987  2020-09-12      18:40        7   
37         1584    120.193    23.017  2020-09-12      20:30        7   
38         1595    120.193    23.017  2020-09-13      12:08        1   
39         1605    120.193    23.009  2020-09-13      12:10        1   
40         1626    120.193    22.993  2020-09-13      13:10        1   
41         1709    120.283    22.922  2020-09-13      13:54        1   
42         1726    120.279    23.148  2020-09-13      14:36        1   
43         1847    120.666    24.296  2020-09-13      15:15        1   
44         1998    121.563    25.087  2020-09-13      16:38        1   
45         2019    121.563    25.087  2020-09-13      19:07        1   
46         2447    121.576    24.986  2020-09-13      19:58        1   
47         2477    121.576    24.986  2020-09-13      20:28        1   
48         2588    121.563    25.087  2020-09-13      20:52        1   
49         2613    121.563    25.087  2020-09-14      12:11        2   
50         2699    121.616    25.057  2020-09-14      12:41        2   
51         2730    121.616    25.057  2020-09-14      17:22        2   
52         2855    121.576    24.986  2020-09-14      17:48        2   

          duration      speed  \
0   1 day, 1:00:00        NaN   
1   1 day, 1:00:00        NaN   
2         11:25:

## Map Category

In [705]:
stopLoc = pd.merge(stopLoc, loc_to_cat, how='left', on='category1' )
stopLoc = stopLoc.drop(['name1','category1','location_id'],1)
stopLoc['user_id'] = 2
stopLoc = stopLoc[['user_id','weekday','start_time','duration','location']]
stopLoc
#把start_date加回來
#name1,category1拿掉 place_cat對表換成數字

user_id  weekday start_time        duration  location
0         2        4      11:00  1 day, 1:00:00       NaN
1         2        5      12:00  1 day, 1:00:00       NaN
2         2        6    13:00\n        11:25:00       NaN
3         2        5      00:25        10:45:00       NaN
4         2        5      11:10         0:36:00       NaN
5         2        5      11:46         0:11:00       NaN
6         2        5      11:57         0:47:00       5.0
7         2        5      12:44         5:55:00       4.0
8         2        5      18:39         0:19:00       NaN
9         2        5      18:58         0:13:00       5.0
10        2        5      19:11         0:20:00       5.0
11        2        5      19:31         0:26:00       NaN
12        2        5      19:57         1:13:00       6.0
13        2        5      21:10        12:05:00       1.0
14        2        6      09:15         0:30:00       NaN
15        2        6      09:45         1:19:00       NaN
16        2        6      11:04         1:07:00       NaN
17        2        6      12:11         1:47:00       NaN
18        2        6      13:58         1:08:00       NaN
19        2        6      15:06         0:48:00       5.0
20        2        6      15:54         0:55:00       5.0
21        2        6      16:49         0:31:00       NaN
22        2        6      17:20         1:23:00       NaN
23        2        6      18:43         0:38:00       5.0
24        2        6      19:21         0:17:00       5.0
25        2        6      19:38         0:53:00      19.0
26        2        6      20:31         2:10:00       NaN
27        2        6      22:41         1:58:00       NaN
28        2        7      00:39         2:11:00       6.0
29        2        7      02:50         9:00:00       NaN
30        2        7      11:50         0:17:00       NaN
31        2        7      12:07         1:49:00       5.0
32        2        7      13:56         2:28:00       NaN
33        2        7      16:24         0:18:00       6.0
34        2        7      16:42         0:31:00       4.0
35        2        7      17:13         1:27:00       5.0
36        2        7      18:40         1:50:00       5.0
37        2        7      20:30        15:38:00       1.0
38        2        1      12:08         0:02:00       NaN
39        2        1      12:10         1:00:00       6.0
40        2        1      13:10         0:44:00       NaN
41        2        1      13:54         0:42:00       NaN
42        2        1      14:36         0:39:00       NaN
43        2        1      15:15         1:23:00       NaN
44        2        1      16:38         2:29:00       1.0
45        2        1      19:07         0:51:00       NaN
46        2        1      19:58         0:30:00       3.0
47        2        1      20:28         0:24:00       NaN
48        2        1      20:52        15:19:00       1.0
49        2        2      12:11         0:30:00       NaN
50        2        2      12:41         4:41:00       NaN
51        2        2      17:22         0:26:00       NaN
52        2        2      17:48        20:51:00       3.0

In [497]:
traing = stopLoc.iloc[:, np.r_[0:4]].values
predictions = clf.predict(traing)

ValueError: could not convert string to float: '11:00'

## Myplace

In [ ]:
savedplace = pd.read_csv("savedPlace.csv")
savedplace['place_longitude'] = round(saveplace['place_longitude'],3)
savedplace['place_latitude'] = round(saveplace['place_latitude'],3)
#savedplace = savedplace.loc[savedplace['my_place'] == 1]
savedplace = savedplace.drop(['place_name','my_place','place_id'],1)
savedplace = savedplace.rename(columns={"place_longitude": "longitude", "place_latitude": "latitude"})
savedplace = savedplace.drop_duplicates(subset=['longitude', 'latitude'], keep='last')
savedplace.head()

In [ ]:
stopLoc = pd.merge(stopLoc, savedplace, how='left', on=['longitude','latitude'])
stopLoc